In [1]:
#!/usr/bin/python
import talib
import requests
import calendar
import pandas as pd
import numpy as np
import python_bitbankcc
from datetime import datetime,date, timedelta
import matplotlib.pyplot as plt
import matplotlib.dates as mdates
from matplotlib.dates import DateFormatter
%matplotlib notebook

In [2]:
start_day = "20200401"
start_dt = datetime.strptime(start_day, "%Y%m%d")
end_day = "20200810"
end_dt = datetime.strptime(end_day, "%Y%m%d")
dt = start_dt

In [3]:
API = python_bitbankcc.public()
pair = 'btc_jpy'
period = '1min' # 1min, 5min, 15min, 30min, 1hour, 4hour, 8hour, 12hour, 1day, 1week
ohlcv = []
while dt <= end_dt:
    ohlcv.extend(API.get_candlestick(pair, period, datetime.strftime(dt, "%Y%m%d"))['candlestick'][0]['ohlcv'])
    dt = dt + timedelta(days=1)
df = pd.DataFrame(ohlcv, columns = ['Open', 'High', 'Low', 'Close', 'Volume', 'Time'])
df['Time'] = [datetime.fromtimestamp(float(time)/1000) for time in df['Time']]
df.drop('Volume', axis=1, inplace=True)
df.set_index('Time', inplace=True)
print('length of ohlcv: {}'.format(len(ohlcv)))
df.tail()

length of ohlcv: 190080


Open     High      Low    Close
Time                                                   
2020-08-10 23:55:00  1259807  1259808  1259807  1259808
2020-08-10 23:56:00  1259808  1260903  1259808  1260903
2020-08-10 23:57:00  1260903  1260903  1260858  1260861
2020-08-10 23:58:00  1260863  1261347  1260863  1261347
2020-08-10 23:59:00  1261986  1262000  1261497  1261999

In [4]:
df['Open'] = df['Open'].astype(np.int64)
df['High'] = df['High'].astype(np.int64)
df['Low'] = df['Low'].astype(np.int64)
df['Close'] = df['Close'].astype(np.int64)

In [5]:
from backtesting import Strategy

def EmaDisparity(data, n):
    df = pd.DataFrame({'Open': data.Open, 'High': data.High, 'Low': data.Low, 'Close': data.Close})
    df['Ema'] = talib.EMA(df['Close'], timeperiod=n)
    df['Dis'] = (df['Close'] - df['Ema'])/df['Close']
    disparity = pd.Series(df['Dis'])
    return disparity

def Std(data, n):
    df = pd.DataFrame({'Open': data.Open, 'High': data.High, 'Low': data.Low, 'Close': data.Close})
    df['Std'] = df['Close'].rolling(n).std().fillna(df['Close'].rolling(n).std().mean())
    std = pd.Series(df['Std'])
    return std

class DisparityStrategy(Strategy):
    
    # Define the period for sma disparity and std
    # Reference: https://in.tradingview.com/script/MhXqOtpr/
    n = 8
    std_ = 1500.0
    dis_l = 0.0008 # 0.0001 is hundreds yen unit order
    dis_h = 0.0013 # 0.0001 is hundreds yen unit order
    
    def init(self):
        # Precompute two moving averages
        self.dis = self.I(EmaDisparity, self.data, self.n)
        self.std = self.I(Std, self.data, self.n)
    
    def next(self):
        if self.std > self.std_:
            if self.dis >= self.dis_l and self.dis <= self.dis_h:
                self.position.close()
                self.sell()
            elif self.dis <= -self.dis_l and self.dis >= -self.dis_h:
                self.position.close()
                self.buy()
            else:
                if self.position:
                    self.position.close()
        else:
            if self.position:
                self.position.close()

/opt/conda/lib/python3.7/site-packages/backtesting/_plotting.py:44: UserWarning: Jupyter Notebook detected. Setting Bokeh output to notebook. This may not work in Jupyter clients without JavaScript support (e.g. PyCharm, Spyder IDE). Reset with `backtesting.set_bokeh_output(notebook=False)`.
  warnings.warn('Jupyter Notebook detected. '


Loading BokehJS ...

In [6]:
from backtesting import Backtest
# start from 1 BTC with the commission 0.12%

df_ = df.copy()
bt = Backtest(df_[:50000], DisparityStrategy, cash=1, commission=.0012, trade_on_close=True)
bt.run()

Start                     2020-04-01 00:00:00
End                       2020-05-05 17:19:00
Duration                     34 days 17:19:00
Exposure [%]                         0.934019
Equity Final [$]                     0.572339
Equity Peak [$]                       1.00091
Return [%]                           -42.7661
Buy & Hold Return [%]                 36.8693
Max. Drawdown [%]                    -42.8181
Avg. Drawdown [%]                    -42.8181
Max. Drawdown Duration       34 days 03:40:00
Avg. Drawdown Duration       34 days 03:40:00
# Trades                                  467
Win Rate [%]                          12.6338
Best Trade [%]                       0.651142
Worst Trade [%]                     -0.704525
Avg. Trade [%]                       -0.11933
Max. Trade Duration           0 days 00:01:00
Avg. Trade Duration           0 days 00:01:00
Expectancy [%]                       0.144473
SQN                                  -18.2889
Sharpe Ratio                      

In [7]:
bt.plot()

In [8]:
%time

n = list(range(6, 8))
std = list(range(100, 1500, 100))
dis_l = [0.0008, 0.0013, 0.0018]
dis_h = [0.0008, 0.0013, 0.0018]
stats = bt.optimize(n=n, std_=std, dis_l=dis_l, dis_h=dis_h, maximize='Equity Final [$]', constraint=lambda param: param.dis_l < param.dis_h)
print(stats)

CPU times: user 0 ns, sys: 0 ns, total: 0 ns
Wall time: 5.72 µs


Start                                                   2020-04-01 00:00:00
End                                                     2020-05-05 17:19:00
Duration                                                   34 days 17:19:00
Exposure [%]                                                       0.946019
Equity Final [$]                                                   0.577527
Equity Peak [$]                                                           1
Return [%]                                                         -42.2473
Buy & Hold Return [%]                                               36.8693
Max. Drawdown [%]                                                  -42.2473
Avg. Drawdown [%]                                                  -42.2473
Max. Drawdown Duration                                     34 days 16:59:00
Avg. Drawdown Duration                                     34 days 16:59:00
# Trades                                                                473
Win Rate [%]

In [9]:
stats._strategy

<Strategy DisparityStrategy(n=6,std_=1400,dis_l=0.0008,dis_h=0.0013)>

In [10]:
stats.tail()

SQN                                                       -12.6776
Sharpe Ratio                                             -0.646799
Sortino Ratio                                            -0.959881
Calmar Ratio                                           -0.00274197
_strategy        DisparityStrategy(n=6,std_=1400,dis_l=0.0008,d...
dtype: object